In [1]:
import sqlite3
import os
import sys

dim = 128   #32 o 64
dir = 'itwac'

parent_dir = os.path.abspath(os.path.join(os.getcwd(), os.pardir))

sql_path = f'{parent_dir}/{dir}/itwac{dim} (1).sqlite'
txt_path = f'{parent_dir}/{dir}/itwac{dim} (1).txt'
conllu_dir = 'data/profiling_output/11325'

In [2]:
con = sqlite3.connect(sql_path)

In [3]:
cur = con.cursor()

In [4]:
with open(txt_path, 'w+') as out_file:
    for embedding in cur.execute("SELECT * FROM store"):
        str_embedding = [str(el) for el in embedding[:-1]]
        out_file.write('\t'.join(str_embedding)+'\n')

out_file.close()

In [5]:
embeddings_dim = 128
embeddings_path = f'itwac/itwac{embeddings_dim} (1).txt'

In [6]:
sys.path.append('..')  # Add parent directory to the Python path
from utils.helpers import *

In [7]:
embeddings = load_word_embeddings(parent_dir+"/"+embeddings_path) 

In [24]:
embeddings['vedersi']

array([ 0.09829128, -0.00466396,  0.12274315, -0.00645867,  0.02171866,
       -0.01775092,  0.20173289, -0.0126764 , -0.13903011,  0.14330961,
        0.15038787, -0.00662153,  0.03522438,  0.05580687, -0.06235559,
        0.16190079,  0.13125402,  0.09466209, -0.02967671,  0.06027041,
        0.00226344, -0.04958551,  0.14477645, -0.12636545, -0.07517902,
       -0.0059378 , -0.15247029, -0.07902947,  0.05534033, -0.06163132,
       -0.04358011, -0.11407799, -0.05476963,  0.00276546,  0.04666484,
       -0.02525456,  0.12073468,  0.14676426, -0.00958022,  0.05849574,
       -0.13112271, -0.04931208,  0.05483235, -0.00634756, -0.21491098,
        0.05190172,  0.1771792 ,  0.02620396,  0.06802528, -0.08378372,
        0.0625739 ,  0.04612483, -0.12579846, -0.05673553, -0.02175681,
       -0.19563943,  0.08836281,  0.09511665,  0.1184418 , -0.09940016,
        0.05089193, -0.0161554 ,  0.04401183, -0.03545505,  0.04018058,
        0.13875584,  0.10942651,  0.03830871,  0.08303873,  0.01

In [25]:
import os
all_documents_paths = []
for file_name in os.listdir(conllu_dir):
    file_path = os.path.join(conllu_dir, file_name)
    all_documents_paths.append(file_path)

In [26]:
all_documents = []

for document_path in all_documents_paths:
    document_tokens = get_tokens_from_file(document_path)
    all_documents.append(document_tokens)

In [27]:
all_documents


[[{'word': 'Bella', 'pos': 'PROPN'},
  {'word': 'Tommy', 'pos': 'PROPN'},
  {'word': 'come', 'pos': 'ADP'},
  {'word': 'butta', 'pos': 'NOUN'},
  {'word': '?', 'pos': 'PUNCT'},
  {'word': 'Ho', 'pos': 'AUX'},
  {'word': 'saputo', 'pos': 'VERB'},
  {'word': 'che', 'pos': 'SCONJ'},
  {'word': 'stai', 'pos': 'NOUN'},
  {'word': 'entrando', 'pos': 'VERB'},
  {'word': 'in', 'pos': 'ADP'},
  {'word': '@dgª', 'pos': 'PROPN'},
  {'word': 'e', 'pos': 'CCONJ'},
  {'word': 'che', 'pos': 'PRON'},
  {'word': 'ai', 'pos': 'ADP'},
  {'word': 'strizza', 'pos': 'NOUN'},
  {'word': 'soprattutto', 'pos': 'ADV'},
  {'word': 'su', 'pos': 'ADP'},
  {'word': 'italiano', 'pos': 'NOUN'},
  {'word': 'e', 'pos': 'CCONJ'},
  {'word': 'nei', 'pos': 'ADP'},
  {'word': 'compiti', 'pos': 'NOUN'},
  {'word': 'di', 'pos': 'ADP'},
  {'word': 'scrittura', 'pos': 'NOUN'},
  {'word': '.', 'pos': 'PUNCT'},
  {'word': 'Sai', 'pos': 'VERB'},
  {'word': 'che', 'pos': 'SCONJ'},
  {'word': 'ti', 'pos': 'PRON'},
  {'word': 'dico'

In [28]:
def compute_embeddings_mean(document_embeddings):
    sum_array = np.sum(document_embeddings, axis=0)
    mean_array = np.divide(sum_array, len(document_embeddings))
    return mean_array


def compute_all_embeddings_mean(document_tokens):
    document_embeddings = []
    
    for token in document_tokens:
        word = token['word']
        if word in embeddings:
            document_embeddings.append(embeddings[word])
    
    if len(document_embeddings) == 0:
        mean_document_embeddings = np.zeros(embeddings_dim)
    else:
        mean_document_embeddings = compute_embeddings_mean(document_embeddings)
    return mean_document_embeddings


def compute_filtered_embeddings_mean(document_tokens):
    document_embeddings = []
    
    for token in document_tokens:
        word = token['word']
        pos = token['pos']
        if word in embeddings and pos in ['ADJ', 'NOUN', 'VERB']:
            document_embeddings.append(embeddings[word])
    
    if len(document_embeddings) == 0:
        mean_document_embeddings = np.zeros(embeddings_dim)
    else:
        mean_document_embeddings = compute_embeddings_mean(document_embeddings)
    return mean_document_embeddings


def compute_filtered_embeddings_sep_means(document_tokens):
    adj_embeddings = []
    noun_embeddings = []
    verb_embeddings = []
    
    for token in document_tokens:
        word = token['word']
        pos = token['pos']
        if word in embeddings and pos in ['ADJ']:
            adj_embeddings.append(embeddings[word])
        elif word in embeddings and pos in ['NOUN']:
            noun_embeddings.append(embeddings[word])
        elif word in embeddings and pos in ['VERB']:
            verb_embeddings.append(embeddings[word])
    
    if len(adj_embeddings) == 0:
        mean_adj_embeddings = np.zeros(embeddings_dim)
    else:
        mean_adj_embeddings = compute_embeddings_mean(adj_embeddings)
        
    if len(noun_embeddings) == 0:
        mean_noun_embeddings = np.zeros(embeddings_dim)
    else:
        mean_noun_embeddings = compute_embeddings_mean(noun_embeddings)
        
    if len(verb_embeddings) == 0:
        mean_verb_embeddings = np.zeros(embeddings_dim)
    else:
        mean_verb_embeddings = compute_embeddings_mean(verb_embeddings)  
    
    
    mean_document_embeddings = np.concatenate([mean_adj_embeddings, mean_noun_embeddings, mean_verb_embeddings], axis=None)
    return mean_document_embeddings

In [51]:
def extract_features(documents):
    dataset_features = []
    for document_tokens in documents:
        # document_embeddings = compute_all_embeddings_mean(document_tokens)
        document_embeddings = compute_all_embeddings_mean(document_tokens)
        # document_embeddings = compute_filtered_embeddings_sep_means(document_tokens)
        dataset_features.append(document_embeddings)
    return dataset_features

In [52]:
all_features = extract_features(all_documents)


In [53]:
len(all_features), len(all_features[0])


(400, 128)

In [54]:
all_labels = create_label_list(all_documents_paths)


In [55]:
def train_test_split(all_features, all_labels, all_documents_paths):
    train_features, train_labels = [], []
    test_features, test_labels = [], []
    
    for features, label,  document_path in zip(all_features, all_labels, all_documents_paths):
        if 'training' in document_path:
            train_features.append(features)
            train_labels.append(label)
        else:
            test_features.append(features)
            test_labels.append(label)
    return train_features, train_labels, test_features, test_labels


In [56]:
train_features, train_labels, test_features, test_labels = train_test_split(all_features, all_labels, all_documents_paths)
len(train_features), len(train_labels), len(test_features), len(test_labels)

(200, 200, 200, 200)

In [57]:
len(train_labels)

200

In [58]:
from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler()
# X_train = np.stack(train_features, axis=0)
X_train = scaler.fit_transform(train_features)

In [59]:
from sklearn.model_selection import GridSearchCV
from sklearn.svm import LinearSVC

# Define the parameter grid to search through
param_grid = {
    'C': [0.1, 0.01, 0.001],  # Regularization parameter
    'dual': [True, False]
}

# Initialize SVM with linear kernel
svc = LinearSVC()

# Initialize GridSearchCV with 5-fold cross-validation
grid_search = GridSearchCV(estimator=svc, param_grid=param_grid, cv=5, refit=True)

# Fit the grid search to your data
grid_search.fit(X_train, train_labels)

# Get mean test scores across folds
mean_test_scores = grid_search.cv_results_['mean_test_score']

# Print the best parameters and best score
print("Best parameters found:", grid_search.best_params_)
print("Best score found:", grid_search.best_score_)

Best parameters found: {'C': 0.1, 'dual': True}
Best score found: 0.6


In [60]:
X_test = scaler.transform(test_features)
# Get the best estimator (model) found by grid search
best_model = grid_search.best_estimator_

# Now, you can use this best_model to make predictions on new data
# For example, if you have new data X_new, you can predict its labels as follows:
predictions = best_model.predict(X_test)

In [61]:
from sklearn.metrics import classification_report, ConfusionMatrixDisplay, confusion_matrix
test_predictions = predictions
print(classification_report(test_labels, test_predictions, zero_division=0)) # output_dict=True

              precision    recall  f1-score   support

           F       0.55      0.70      0.61       100
           M       0.58      0.42      0.49       100

    accuracy                           0.56       200
   macro avg       0.57      0.56      0.55       200
weighted avg       0.57      0.56      0.55       200

